# Tutorial: Working with IRIS and GPS Coordinates

This Jupyter Notebook is a tutorial that demonstrates how to work with IRIS codes and GPS coordinates. Each cell in this notebook is independently executable, allowing you to run and test each step separately.

### Get the iris code for the corresponding gps coordinates

In [3]:
from iris_insee_utils import gps_to_code_iris

gps_to_code_iris(2.30, 48.81, iris_year=2018)

'920200101'

### More information about an iris from gps coordinates

In [4]:
from iris_insee_utils import gps_to_iris

gps_to_iris(2.30, 48.81, iris_year=2018)

CODE_IRIS    NOM_IRIS TYP_IRIS
0  920200101  République        H

In [5]:
gps_to_iris(2.30, 48.81, iris_year=2018, iris_full_info=True)

geometry  index_right INSEE_COM    NOM_COM  IRIS  CODE_IRIS  \
0  POINT (2.3 48.81)         3639     92020  Châtillon  0101  920200101   

     NOM_IRIS TYP_IRIS  
0  République        H

#### Get iris codes from a dataframe of gps coordinates

In [12]:
import pandas as pd

from iris_insee_utils.gps_coordinates_to_iris import df_gps_to_iris

df = pd.DataFrame({
    "Lieu": ["Mairie de Marseille", "Site-Mémorial du Camp des Milles"],
    "longitude": [      5.369,      5.382  ],  "latitude": [      43.296,      43.503  ],
    })
df_iris_insee = df_gps_to_iris(df, "longitude", "latitude", iris_year=2020)
df_iris_insee

Lieu longitude latitude  IRIS  CODE_IRIS  \
0               Mairie de Marseille     5.369   43.296  0301  132020301   
1  Site-Mémorial du Camp des Milles     5.382   43.503  0905  130010905   

             NOM_IRIS  
0        Quai du Port  
1  Les Milles Village

In [ ]:
### Plot data at the IRIS level

##[Couples - Familles - Ménages en 2020](https://www.insee.fr/fr/statistiques/7704086)
import pandas as pd

from iris_insee_utils import plot_folium_map

url="https://github.com/adrienpacifico/iris_insee_utils_data/raw/refs/heads/main/data/raw/other_data/insee_data/base-ic-couples-familles-menages-2020.CSV"


df_enrich=pd.read_csv(url, sep=";",
            )

plot_folium_map(
    2020,
    "Paris",
    #df_oi=df_bus_stops.drop_duplicates(subset="name"),
    df_enrich=df_enrich.rename(columns={"C20_MEN": "Nombre de ménges",
                                        "C20_PMEN": "Nombre de personnes"}),
    df_enrich_iriscol_colname="IRIS",
    df_enrich_select_cols=["Nombre de ménges","Nombre de personnes"],
)

/var/folders/l5/p4f2y4qd0jj4n34zysyp82540000gn/T/ipykernel_38508/1011073676.py:9: DtypeWarning: Columns (0,1,3) have mixed types. Specify dtype option on import or set low_memory=False.
  df_enrich=pd.read_csv(url, sep=";"
/Users/adrienpacifico/Projects/iris_insee_utils/iris_insee_utils/iris_map.py:72: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[df_map.geometry.centroid.y.mean(), df_map.geometry.centroid.x.mean()],


### Plot with data of interest (gps coordinates), and enriching data.

In [11]:
%pip install overpy
import overpy
import pandas as pd

from iris_insee_utils import plot_folium_map

# Initialize the Overpass API
api = overpy.Overpass()

# Define the Overpass query to get bus stops in Marseille
query = """
[out:json];
area["name"="Limoges"]->.searchArea;
node["highway"="bus_stop"](area.searchArea);
out body;
"""

# Execute the query
result = api.query(query)

# Extract data from the result
data = []
for node in result.nodes:
    data.append({
        #"id": node.id,
        "lat": node.lat,
        "lon": node.lon,
        "name": node.tags.get("name", "N/A"),
        "highway": node.tags.get("highway", "N/A"),
        #"operator": node.tags.get("operator", "N/A")
    })

# Convert the data to a pandas DataFrame
df_bus_stops = pd.DataFrame(data).drop_duplicates(subset="name")

Note: you may need to restart the kernel to use updated packages.


In [ ]:
plot_folium_map(2020, "Limoges", df_oi=df_bus_stops)

/Users/adrienpacifico/Projects/iris_insee_utils/iris_insee_utils/iris_map.py:72: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[df_map.geometry.centroid.y.mean(), df_map.geometry.centroid.x.mean()],
